# 2025-02-24 Check expected pos L2 loss for different init E, to select proper time_window for optimization

In [1]:
import numpy as np 
import os 
import os.path as osp

In [2]:
# create log directory by date
from datetime import datetime
today = datetime.today().strftime('%Y%m%d')
log_dir = osp.join('logs', today)
os.makedirs(log_dir, exist_ok=True)

In [3]:
data_path = "/data/ruihan/projects/PhysDreamer/projects/inference/output/carnations/demos"
pos_data = {}
for initE in [1000000, 5000000, 8000000]:
    pos_path = osp.join(data_path, f"inference_demo_carnation_sv_gres64_substep768_eval_ys_{initE:.1f}_force_0_mag_1e-05_point_0_velo_1.0_hf_grid_pos.npy")
    print(f"Load pos data from {pos_path}")
    pos_data[initE] = np.load(pos_path)
    print(pos_data[initE].shape)


Load pos data from /data/ruihan/projects/PhysDreamer/projects/inference/output/carnations/demos/inference_demo_carnation_sv_gres64_substep768_eval_ys_1000000.0_force_0_mag_1e-05_point_0_velo_1.0_hf_grid_pos.npy
(91, 5337, 3)
Load pos data from /data/ruihan/projects/PhysDreamer/projects/inference/output/carnations/demos/inference_demo_carnation_sv_gres64_substep768_eval_ys_5000000.0_force_0_mag_1e-05_point_0_velo_1.0_hf_grid_pos.npy
(91, 5337, 3)
Load pos data from /data/ruihan/projects/PhysDreamer/projects/inference/output/carnations/demos/inference_demo_carnation_sv_gres64_substep768_eval_ys_8000000.0_force_0_mag_1e-05_point_0_velo_1.0_hf_grid_pos.npy
(91, 5337, 3)


In [7]:
# Visualize three point cloud at certain frame and compute the difference

# import matplotlib.pyplot as plt
# from mpl_toolkits.mplot3d import Axes3D

# fig = plt.figure()
# ax = fig.add_subplot(111, projection='3d')
# for initE in [1000000, 5000000, 8000000]:
#     pos = pos_data[initE][frame]
#     ax.scatter(pos[:,0], pos[:,1], pos[:,2], label=f"initE={initE/1e6}e6", s=0.1)
# ax.legend()
# plt.show()


# interactive plot
import plotly.graph_objects as go

for frame in [6]:
    colors = ['red', 'green', 'blue']  # Different colors for each point cloud

    fig = go.Figure()

    for i, initE in enumerate([1000000, 5000000, 8000000]):
        pos = pos_data[initE][frame]
        fig.add_trace(go.Scatter3d(
            x=pos[:, 0], y=pos[:, 1], z=pos[:, 2],
            mode='markers',
            marker=dict(size=1, color=colors[i]),  # Assign color and small marker size
            name=f"initE={initE/1e6}e6"
        ))

    # Compute mean square error between each point cloud with initE = 5000000
    l2_error0 = np.mean((pos_data[1000000][frame] - pos_data[5000000][frame])**2, axis=1)
    l2_error1 = np.mean((pos_data[8000000][frame] - pos_data[5000000][frame])**2, axis=1)
    print(f"L2 error between initE=5000000 and initE=1000000: {l2_error0.mean()}, shape {l2_error0.shape}")
    print(f"L2 error between initE=5000000 and initE=8000000: {l2_error1.mean()}, shape {l2_error1.shape}")

    # Add annotation (text box) in 3D space
    fig.add_annotation(
        text=f"L2 error - initE=1e6: {l2_error0.mean()}, initE=8e6 {l2_error1.mean()}",  # Your annotation text
        x=0.5, y=-0.15,  # x=0.5 centers it, y<0 moves it below the plot
        xref="paper", yref="paper",  # Paper reference (not data space)
        showarrow=False,  # No arrow
        font=dict(size=14, color="black"),
        align="center",
        bgcolor="white", bordercolor="white", borderwidth=1
    )

    # Update layout for better visualization
    fig.update_layout(
        scene=dict(
            xaxis_title='X',
            yaxis_title='Y',
            zaxis_title='Z'
        ),
        title=f"Interactive 3D Point Clouds, frame={frame}",
        width=800, height=600
    )

    # save the figure
    output_path = osp.join(log_dir, f"3d_point_cloud_differentE_frame_{frame}")
    fig.write_html(f"{output_path}.html")
    fig.write_image(f"{output_path}.png", width=800, height=600)

    fig.show()

L2 error between initE=5000000 and initE=1000000: 3.43523858248318e-08, shape (5337,)
L2 error between initE=5000000 and initE=8000000: 3.098516332400436e-09, shape (5337,)


# 2025-02-25 Check actual pos L2 loss for different initE

In [12]:
train_pos_data = {}
l2_error = {}
train_log_parent_path = "/data/ruihan/projects/PhysDreamer/projects/train/output/inverse_sim"
step = 0
start_time_idx = 5

colors = ['red', 'green', 'blue']  # Different colors for each point cloud
fig = go.Figure()

for color, initE in zip(colors, [0.1, 0.5, 0.8]):
    train_log_gaussian_path = osp.join(train_log_parent_path, f"mat_force_lr_0.001_lf_1e-5_initE_{initE}_lambda_0.0_0.0_0.0_0.0_1.0_0.0/seed0/gaussian_pos_{step:06d}_{start_time_idx:02d}.npy")
    train_log_gt_path = osp.join(train_log_parent_path, f"mat_force_lr_0.001_lf_1e-5_initE_{initE}_lambda_0.0_0.0_0.0_0.0_1.0_0.0/seed0/gt_pos_{step:06d}_{start_time_idx:02d}.npy")
    train_log_gaussian_pos = np.load(train_log_gaussian_path)
    train_log_gt_pos = np.load(train_log_gt_path)
    train_pos_data[initE] = train_log_gaussian_pos
    print(f"initE = {initE}, train_log_gaussian_pos shape: {train_log_gaussian_pos.shape}, train_log_gt_pos shape: {train_log_gt_pos.shape}") # [5337, 3]
    # compute mean square error
    error = np.mean((train_log_gaussian_pos - train_log_gt_pos)**2, axis=1)
    print(f"L2 error between gaussian pos and gt pos: {error.mean()}, shape {error.shape}")
    l2_error[initE] = error

    # visualize the difference. plot the gt in black and gaussian in color
    fig.add_trace(go.Scatter3d(
        x=train_log_gt_pos[:, 0], y=train_log_gt_pos[:, 1], z=train_log_gt_pos[:, 2],
        mode='markers',
        marker=dict(size=1, color='black'),  # Assign color and small marker size
        name=f"initE=gt"
    ))

    fig.add_trace(go.Scatter3d(
        x=train_log_gaussian_pos[:, 0], y=train_log_gaussian_pos[:, 1], z=train_log_gaussian_pos[:, 2],
        mode='markers',
        marker=dict(size=1, color=color),  # Assign color and small marker size
        name=f"initE={initE}e6 gaussian"
    ))

# Add annotation (text box) in 3D space
fig.add_annotation(
    text=f"L2 error - initE=1e6: {l2_error[0.1].mean()}, initE=8e6 {l2_error[0.8].mean()}",  # Your annotation text
    x=0.5, y=-0.15,  # x=0.5 centers it, y<0 moves it below the plot
    xref="paper", yref="paper",  # Paper reference (not data space)
    showarrow=False,  # No arrow
    font=dict(size=14, color="black"),
    align="center",
    bgcolor="white", bordercolor="white", borderwidth=1
)

# Update layout for better visualization
fig.update_layout(
    scene=dict(
        xaxis_title='X',
        yaxis_title='Y',
        zaxis_title='Z'
    ),
    title=f"Interactive 3D - training, frame={start_time_idx+1}",
    width=800, height=600
)

# save the figure
output_path = osp.join(log_dir, f"3d_training_differentE_frame_{start_time_idx+1}")
fig.write_html(f"{output_path}.html")
fig.write_image(f"{output_path}.png", width=800, height=600)

fig.show()

initE = 0.1, train_log_gaussian_pos shape: (5337, 3), train_log_gt_pos shape: (5337, 3)
L2 error between gaussian pos and gt pos: 3.434574225025244e-08, shape (5337,)
initE = 0.5, train_log_gaussian_pos shape: (5337, 3), train_log_gt_pos shape: (5337, 3)
L2 error between gaussian pos and gt pos: 5.001125381876026e-13, shape (5337,)
initE = 0.8, train_log_gaussian_pos shape: (5337, 3), train_log_gt_pos shape: (5337, 3)
L2 error between gaussian pos and gt pos: 3.0493403357922944e-09, shape (5337,)
